In [2]:
import pandas as pd
import sqlalchemy as sal
import numpy as np
import geopandas as gpd

import folium
from shapely.geometry import mapping
from folium.plugins import MarkerCluster, LocateControl, Fullscreen

In [6]:
%store -r all_years_data
%store -r subgroups
%store -r tests
%store -r meta

In [9]:
tests.head(2)

Test ID  Test ID Num                            Test Name
0        1            1  SB - English Language Arts/Literacy
1        2            2                     SB - Mathematics

In [13]:
subgroups.sort_values(by='Student Group')

Demographic ID  Demographic ID Num  \
0                1                   1   
28             128                 128   
24              99                  99   
7               31                  31   
25             111                 111   
5                8                   8   
33             180                 180   
3                6                   6   
32             170                 170   
31             160                 160   
4                7                   7   
29             142                 142   
34             190                 190   
26             120                 120   
18              80                  80   
17              79                  79   
14              76                  76   
15              77                  77   
13              75                  75   
12              74                  74   
30             144                 144   
16              78                  78   
36             201                 201   
37             202                 202   
42             207                 207   
39             204                 204   
40             205                 205   
41             206                 206   
38             203                 203   
35             200                 200   
43             220                 220   
44             221                 221   
45             222                 222   
46             223                 223   
47             224                 224   
48             225                 225   
50             227                 227   
49             226                 226   
2                4                   4   
1                3                   3   
11              53                  53   
10              52                  52   
6               28                  28   
9               51                  51   
8               50                  50   
23              94                  94   
22              93                  93   
21              92                  92   
20              91                  91   
19              90                  90   
27             121                 121   

                                     Demographic Name  \
0                                        All Students   
28                           Students with disability   
24               Students with no reported disability   
7                          Economically disadvantaged   
25                     Not economically disadvantaged   
5       Reclassified fluent English proficient (RFEP)   
33                                       English only   
3          Fluent English proficient and English only   
32                                           Ever-ELs   
31                                    English learner   
4            Initial fluent English proficient (IFEP)   
29  English learners enrolled in school in the U.S...   
34                             To be determined (TBD)   
26  English learners (ELs) enrolled in school in t...   
18                                              White   
17                Native Hawaiian or Pacific Islander   
14                                              Asian   
15                                           Filipino   
13                   American Indian or Alaska Native   
12                          Black or African American   
30                                  Two or more races   
16                                 Hispanic or Latino   
36                   American Indian or Alaska Native   
37                                              Asian   
42                                  Two or more races   
39                                 Hispanic or Latino   
40                Native Hawaiian or Pacific Islander   
41                                              White   
38                                           Filipino   
35                          Black or African American   
43                          Black or African America

In [16]:
all_years_data[all_years_data['school_id'] == '0']

/Users/justinaugust/anaconda3/envs/gadsi/lib/python3.7/site-packages/pandas/core/ops/__init__.py:1115: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


Empty DataFrame
Columns: [school_id, group_1_test_1, group_1_tested, group_1_test_2, group_3_test_1, group_3_tested, group_3_test_2, group_4_test_1, group_4_tested, group_4_test_2, group_6_test_1, group_6_tested, group_6_test_2, group_7_test_1, group_7_tested, group_7_test_2, group_8_test_1, group_8_tested, group_8_test_2, group_28_test_1, group_28_tested, group_28_test_2, group_31_test_1, group_31_tested, group_31_test_2, group_50_test_1, group_50_tested, group_50_test_2, group_51_test_1, group_51_tested, group_51_test_2, group_52_test_1, group_52_tested, group_52_test_2, group_53_test_1, group_53_tested, group_53_test_2, group_74_test_1, group_74_tested, group_74_test_2, group_75_test_1, group_75_tested, group_75_test_2, group_76_test_1, group_76_tested, group_76_test_2, group_77_test_1, group_77_tested, group_77_test_2, group_78_test_1, group_78_tested, group_78_test_2, group_79_test_1, group_79_tested, group_79_test_2, group_80_test_1, group_80_tested, group_80_test_2, group_90_test_1, group_90_tested, group_90_test_2, group_91_test_1, group_91_tested, group_91_test_2, group_92_test_1, group_92_tested, group_92_test_2, group_93_test_1, group_93_tested, group_93_test_2, group_94_test_1, group_94_tested, group_94_test_2, group_99_test_1, group_99_tested, group_99_test_2, group_111_test_1, group_111_tested, group_111_test_2, group_120_test_1, group_120_tested, group_120_test_2, group_121_test_1, group_121_tested, group_121_test_2, group_128_test_1, group_128_tested, group_128_test_2, group_142_test_1, group_142_tested, group_142_test_2, group_144_test_1, group_144_tested, group_144_test_2, group_160_test_1, group_160_tested, group_160_test_2, group_170_test_1, group_170_tested, group_170_test_2, ...]
Index: []

[0 rows x 158 columns]

In [59]:
cluster_dict = {
    'high': {
        'mask': (all_years_data['group_1_test_1_avg_met_exceeded'] >= 75) & (all_years_data['group_1_test_2_avg_met_exceeded'] >= 75),
        'desc' : 'All Students High Tier Performance',
        'color' : 'green'
    },
    'mid' : {
        'mask': (all_years_data['group_1_test_1_avg_met_exceeded'] >= 50) & (all_years_data['group_1_test_2_avg_met_exceeded'] >= 50)\
            & (all_years_data['group_1_test_1_avg_met_exceeded'] < 75) & (all_years_data['group_1_test_2_avg_met_exceeded'] < 75),
        'desc' : 'All Students Mid Tier Performance',
        'color' : 'beige'
    },
    'low' : {
        'mask': (all_years_data['group_1_test_1_avg_met_exceeded'] < 50) & (all_years_data['group_1_test_2_avg_met_exceeded'] < 50),
        'desc' : 'All Students Low Tier Performance',
        'color' : 'red'
    },
}

In [96]:




#create a group with the name of every filter
maps = {}

all_map = folium.Map(location = [all_years_data['lat'].mean(), all_years_data['lng'].mean()],
                 zoom_start=10,
                  )
for year in set(all_years_data['year'].values):
    mask = False
    year_mask = (all_years_data['year'] == year)
    markers_list = []

    
    maps[year] = folium.Map(location = [year_data['lat'].mean(), year_data['lng'].mean()],
                 zoom_start=10,
                  )
    

    for key in cluster_dict.keys():
        tier_mask = cluster_dict[key]['mask']

        markers_feature_group = folium.FeatureGroup(name = f'{year} - {cluster_dict[key]["desc"]}', show=False)
        marker_cluster = MarkerCluster()
        
        for school in set(all_years_data.loc[year_mask & tier_mask, "school_name"].values):
            school_mask = (all_years_data['school_name'] == school)

            marker_data = all_years_data.loc[year_mask & tier_mask & school_mask]
            
            info = f'<h3>{school}</h3><h4>{year} Data</h4><h5>{cluster_dict[key]["desc"]}</h5>'
            
            if marker_data.shape[0] != 0:
                marker = folium.Marker([marker_data.loc[:, 'lat'].values[0],
                                               marker_data.loc[:, 'lng'].values[0]
                                              ], 
                                               popup = info,
                                               icon = folium.Icon(color = cluster_dict[key]['color'],
                                                                  icon = 'ok-sign'
                                                                 )
                                               )
                marker_cluster.add_child(marker)

            markers_feature_group.add_child(marker_cluster)
            markers_list.append(markers_feature_group)

    for feature_group in markers_list:
        maps[year].add_child(feature_group)
        all_map.add_child(feature_group)

    maps[year].add_child(folium.LayerControl())
    maps[year].add_child(LocateControl())
    maps[year].add_child(Fullscreen(position='topleft',
               title='Full Screen',
               title_cancel='Exit Full Screen',
               force_separate_button=True
              ))
    
all_map.add_child(folium.LayerControl())
all_map.add_child(LocateControl())
all_map.add_child(Fullscreen(position='topleft',
           title='Full Screen',
           title_cancel='Exit Full Screen',
           force_separate_button=True
          ))
        


In [92]:
maps

{'2017': <folium.folium.Map at 0x1435a3ad0>,
 '2018': <folium.folium.Map at 0x128ce4d10>,
 '2016': <folium.folium.Map at 0x14b022a90>,
 '2015': <folium.folium.Map at 0x13d2449d0>,
 '2019': <folium.folium.Map at 0x138055290>}

In [93]:
maps['2015']

     |████████████████████████████████| 51kB 608kB/s eta 0:00:01
  Created wheel for pyshp: filename=pyshp-1.1.7-cp37-none-any.whl size=18288 sha256=a6e532e4dc6a5716a6f393b00d17cc6e408ebe2bfe3bbdc9acc802adf10bb492
  Stored in directory: /Users/justinaugust/Library/Caches/pip/wheels/a6/7b/1e/87f41e3ddc2f252506fd57e28abd7982e3b84fa0ea8924a2e0
Successfully built pyshp


In [14]:
#!pip install pyshp==1.1.7
import shapefile
from shapely.geometry import mapping, shape

In [17]:
sf = shapefile.Reader("data/School Boundaries USA/SHP/sample_school_attendance_zone_usa_objects")

In [6]:
shapes = sf.shapes()
records = sf.records()

In [43]:
records[0]

[16004772,
 'CENTRAL ELEMENTARY SCHOOL',
 'School',
 'SAZ',
 'School Attendance Zone',
 'USA',
 'San Francisco, CA',
 37.519196,
 -122.281432,
 '20171205',
 25971652.074]

In [44]:

samples = {records[i][0]: {'id': records[i][0],
                           'name': records[i][1],
                           'city': records[i][6],
                           'shape': shapes[i]} for i in range(len(records))}

In [53]:
df = gpd.GeoDataFrame(pd.DataFrame(samples).T, geometry='shape')
df

id                              name               city  \
16004772  16004772         CENTRAL ELEMENTARY SCHOOL  San Francisco, CA   
16004773  16004773             FOX ELEMENTARY SCHOOL  San Francisco, CA   
16004774  16004774          NESBIT ELEMENTARY SCHOOL  San Francisco, CA   
16004775  16004775             RALSTON MIDDLE SCHOOL  San Francisco, CA   
16004776  16004776        CIPRIANI ELEMENTARY SCHOOL  San Francisco, CA   
...            ...                               ...                ...   
16111620  16111620         SOUTH HILLSBOROUGH SCHOOL  San Francisco, CA   
16111621  16111621          WEST HILLSBOROUGH SCHOOL  San Francisco, CA   
16111622  16111622         NORTH HILLSBOROUGH SCHOOL  San Francisco, CA   
16116066  16116066  SAN MATEO PARK ELEMENTARY SCHOOL  San Francisco, CA   
16117609  16117609          HOOVER ELEMENTARY SCHOOL  San Francisco, CA   

                                                      shape  
16004772  POLYGON ((-122.24356 37.55258, -122.24001 37.5...  
16004773  POLYGON ((-122.24356 37.55258, -122.24001 37.5...  
16004774  POLYGON ((-122.24356 37.55258, -122.24001 37.5...  
16004775  POLYGON ((-122.24356 37.55258, -122.24001 37.5...  
16004776  POLYGON ((-122.24356 37.55258, -122.24001 37.5...  
...                                                     ...  
16111620  POLYGON ((-122.33425 37.53798, -122.33529 37.5...  
16111621  POLYGON ((-122.38034 37.57054, -122.38007 37.5...  
16111622  POLYGON ((-122.37164 37.58060, -122.37147 37.5...  
16116066  MULTIPOLYGON (((-122.33455 37.58040, -122.3293...  
16117609  POLYGON ((-122.39366 37.57016, -122.39422 37.5...  

[192 rows x 4 columns]

In [82]:
for i in range(df.shape[0]):
    shape(df.iloc[i,3])

In [86]:
df_json = mapping(df)

In [85]:
df_json

{'type': 'FeatureCollection',
 'features': [{'id': '16004772',
   'type': 'Feature',
   'properties': {'city': 'San Francisco, CA',
    'id': 16004772,
    'name': 'CENTRAL ELEMENTARY SCHOOL'},
   'geometry': {'type': 'Polygon',
    'coordinates': (((-122.2435555, 37.5525752),
      (-122.2400148, 37.5522896),
      (-122.2331049, 37.5527465),
      (-122.2285363, 37.5517757),
      (-122.2253954, 37.5496627),
      (-122.223977, 37.545935),
      (-122.2297014, 37.5365532),
      (-122.230585, 37.535105),
      (-122.231177, 37.534135),
      (-122.231491, 37.533988),
      (-122.233475, 37.533077),
      (-122.23467, 37.532496),
      (-122.236077, 37.531836),
      (-122.236245, 37.531766),
      (-122.236413, 37.531758),
      (-122.236963, 37.53169),
      (-122.237848, 37.53169),
      (-122.238778, 37.531682),
      (-122.239465, 37.531644),
      (-122.240075, 37.531613),
      (-122.240655, 37.531529),
      (-122.241769, 37.531178),
      (-122.242975, 37.53056),
      (-122.

In [88]:
map_1 = folium.Map(
    zoom_start=10,
    crs = 'EPSG3857',
    control_scale = True,
    prefer_canvas = True,
    max_bounds = True,
    zoom_snap = .5,
    tiles = 'OpenStreetMap'
)
    

schools = folium.Choropleth(
    geo_data = df_json,
    key_on = 'properties.id',
    columns = ['id'],
    fill_color='YlGnBu',
    nan_fill_color = 'white',
    highlight = True,
    name = "School Catchment Areas",
    fill_opacity = 0.7,
    line_opacity = 0.2,
    overlay = True
)
map_1.add_child(schools)

# schools.geojson.add_child(
#     folium.features.GeoJsonTooltip(
#         ['id','name'],
# #             aliases = ['Zip Code',
# #                        'Population (2015)',
# #                        'Population Density (2015)',
# #                        'Occupied Housing Units (2015)'
# #                       ],
#             sticky = False,
#             localize = True,
#                                       )
#     )
        

TypeError: Object of type bytes is not JSON serializable

In [65]:
map_1

TypeError: Object of type bytes is not JSON serializable